In [31]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm
from pymc3.distributions.dist_math import normal_lccdf, normal_lcdf

### Tree and dataframe setup

In [9]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=444,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tbb6678ee7c4b4ecfaa6e24ebd29bdb34" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [10]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [11]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 1.5
𝛽_std = 0.05
𝜓_mean = 0.0
𝜓_std = 0.33
𝜎_std = 0.05

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [12]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  1.536410  0.229932  1.115651
1     0  1.552872  0.026556  0.904660
2     0  1.487890 -0.321123  1.075748
3     0  1.528174 -0.086356  1.094559
4     0  1.503244  0.444541  1.042192

### Generate crossing data

In [13]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

In [14]:
# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

DATA['RI_pooled'] = DATA.intercept + (DATA.b * DATA.dist) + DATA.error
DATA['RI_unpooled'] = DATA.intercept + (DATA.velo * DATA.dist) + DATA.error
DATA['RI_partpooled'] = DATA.intercept + (DATA.velo_x * DATA.dist) + DATA.error

In [16]:
# censor values in range 0-1
DATA.loc[DATA['RI_pooled'] < 0, 'RI_pooled'] = 0
DATA.loc[DATA['RI_pooled'] > 1, 'RI_pooled'] = 1
DATA.loc[DATA['RI_unpooled'] < 0, 'RI_unpooled'] = 0
DATA.loc[DATA['RI_unpooled'] > 1, 'RI_unpooled'] = 1
DATA.loc[DATA['RI_partpooled'] < 0, 'RI_partpooled'] = 0
DATA.loc[DATA['RI_partpooled'] > 1, 'RI_partpooled'] = 1

In [17]:
DATA

sidx0  sidx1      dist         b      velo    velo_x  intercept  \
0         0      1  0.014093  1.569123  1.825611  3.589434   0.058843   
1         0      2  0.093817  1.475324  1.384133  3.666723   0.060876   
2         0      3  0.232354  1.524398  1.667974  3.734608   0.063433   
3         0      4  0.232354  1.568007  2.242480  3.725850   0.080916   
4         0      5  0.234463  1.587113  2.505924  3.761738   0.074592   
...     ...    ...       ...       ...       ...       ...        ...   
3155     76     78  0.057491  1.515498  2.497094 -0.487928   0.030432   
3156     76     79  0.194995  1.430819  1.861327 -0.579221   0.045074   
3157     77     78  0.057491  1.455528  2.218625 -0.729714   0.018721   
3158     77     79  0.194995  1.432789  1.644798 -0.759066   0.117312   
3159     78     79  0.194995  1.552169  2.202481 -0.622859   0.047787   

         error  RI_pooled  RI_unpooled  RI_partpooled  
0     0.003385   0.084341     0.087955       0.112812  
1    -0.006604   0.192683     0.184127       0.398274  
2    -0.013034   0.404600     0.437960       0.918151  
3     0.064646   0.509895     0.666612       1.000000  
4    -0.058734   0.387977     0.603404       0.897845  
...        ...        ...          ...            ...  
3155 -0.105419   0.012141     0.068574       0.000000  
3156 -0.024966   0.299111     0.383057       0.000000  
3157  0.122620   0.225020     0.268891       0.099388  
3158  0.051167   0.447865     0.489205       0.020465  
3159 -0.028711   0.321741     0.448548       0.000000  

[3160 rows x 11 columns]

In [18]:
NSAMPLES = 1000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept     error  \
0      1     26  0.523417  1.570259  1.690114  3.555288   0.037579 -0.025917   
1     33     53  0.555803  1.505988  0.773893  3.082311   0.001843 -0.020690   
2     34     63  1.000000  1.564016  1.027060  1.963146   0.065470 -0.015290   
3     13     67  1.000000  1.458742  1.518098  1.991522   0.042036  0.031772   
4     18     45  0.541446  1.532731  1.904726  3.538284   0.025705  0.091338   

   RI_pooled  RI_unpooled  RI_partpooled  
0   0.833561     0.896295            1.0  
1   0.818186     0.411285            1.0  
2   1.000000     1.000000            1.0  
3   1.000000     1.000000            1.0  
4   0.946935     1.000000            1.0

### Visualize data

In [50]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Pooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_pooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t886b3c7c4d0947fca01b72fe990558d7" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(40.4%,0%,12.2%);fill-opacity:1.0;opacity:0.25;stroke:rgb(0%,0%,0%);stroke-opacity:1.0" transform="translate(299.9999999999999, 50

In [51]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Unpooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_unpooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t77d564c8814c49d99222df9d30d32c95" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <

In [52]:
canvas = toyplot.Canvas(width=350, height=300)
axes = canvas.cartesian(
    label="Partpooled data",
    xlabel="Genetic dist.",
    ylabel="Reprod. incomp.",
)

# points are jittered on x-axis for visibility
axes.scatterplot(
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    size=8,
    opacity=0.25,
    color=SAMPLE.loc[:, 'RI_partpooled'].values,
    mstyle={"stroke": "black"},
);
axes.x.ticks.show = True
axes.y.ticks.show = True

<svg class="toyplot-canvas-Canvas" height="300.0px" id="tfaa4f7c4ccc54a238c47b8c2fd023f6b" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toyplot-Datum" style="fill:rgb(86.2%,42.9%,34.3%);fill-opacity:1.0;opacity:0.25;stroke:rgb(0%,0%,0%);stroke-opacity:1.0" transform="translate(99.98833893042809, 93.91515

### Funcrions to plot results

In [24]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [43]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

### Define models

In [25]:
def censored_pooled_regression(x, y, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5.0, shape=1)

        # linear model prediction
        ri = 𝛼 + 𝛽 * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + 𝛽 * _x_lc, 𝜎, _y_lc),
            )
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + 𝛽 * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [26]:
def censored_unpooled_noncentered_regression(x, y, idx0, idx1, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:
        
        # censored indexers
        sidx0 = pm.Data("spp_idx0", idx0.values[uncensored])
        sidx1 = pm.Data("spp_idx1", idx1.values[uncensored])
        sidx0_u = pm.Data("sidx0_u", idx0.values[upper_censored])
        sidx1_u = pm.Data("sidx1_u", idx1.values[upper_censored])
        sidx0_l = pm.Data("sidx0_l", idx0.values[lower_censored])
        sidx1_l = pm.Data("sidx1_l", idx1.values[lower_censored])

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5., shape=1)
        
        # linear model prediction
        ri = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + (𝛽 + 𝜓[sidx0_l] + 𝜓[sidx1_l]) * _x_lc, 𝜎, _y_lc),
            )
        
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + (𝛽 + 𝜓[sidx0_u] + 𝜓[sidx1_u]) * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [27]:
def censored_partpooled_noncentered_regression(x, y, idx0, idx1, gidx, **kwargs):
    
    # data pre-processing
    lower_censored = y[y <= 0].index
    _x_lc = x[lower_censored].values
    _y_lc = y[lower_censored].values

    upper_censored = y[y >= 1].index
    _x_uc = x[upper_censored].values
    _y_uc = y[upper_censored].values

    uncensored = (y > 0) & (y < 1)
    _x = x[uncensored].values
    _y = y[uncensored].values
    
    # define model
    with pm.Model() as model:
        
        # censored indexers
        sidx0 = pm.Data("spp_idx0", idx0.values[uncensored])
        sidx1 = pm.Data("spp_idx1", idx1.values[uncensored])
        sidx0_u = pm.Data("sidx0_u", idx0.values[upper_censored])
        sidx1_u = pm.Data("sidx1_u", idx1.values[upper_censored])
        sidx0_l = pm.Data("sidx0_l", idx0.values[lower_censored])
        sidx1_l = pm.Data("sidx1_l", idx1.values[lower_censored])
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝜎 = pm.HalfNormal('𝜎', 5., shape=1)
        
        # linear model prediction
        ri = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * _x

        # data likelihood (normal distributed errors)
        y = pm.Normal("y", mu=ri, sigma=𝜎, observed=_y)

        # density of censored data
        if sum(lower_censored):
            lcensored = pm.Potential(
                "lower_censored", 
                normal_lcdf(𝛼 + (𝛽 + 𝜓[sidx0_l] + 𝜓[sidx1_l]) * _x_lc, 𝜎, _y_lc),
            )
        
        if sum(upper_censored):
            ucensored = pm.Potential(
                "upper_censored",
                normal_lccdf(𝛼 + (𝛽 + 𝜓[sidx0_u] + 𝜓[sidx1_u]) * _x_uc, 𝜎, _y_uc),
            )

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Run models

In [28]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=4000,
    draws=4000,
    target_accept=0.95,
    return_inferencedata=False,
    progressbar=True,
)

In [32]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_sub = censored_pooled_regression(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛽, 𝛼]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 92 seconds.


In [33]:
pooled_sub['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  ess_sd  \
𝛼[0]  0.058  0.008   0.042    0.074        0.0      0.0    3993.0  3993.0   
𝛽[0]  1.475  0.017   1.443    1.507        0.0      0.0    4031.0  4028.0   
𝜎[0]  0.057  0.002   0.054    0.060        0.0      0.0    5507.0  5498.0   

      ess_bulk  ess_tail  r_hat  
𝛼[0]    3998.0    4535.0    1.0  
𝛽[0]    4040.0    4563.0    1.0  
𝜎[0]    5553.0    5409.0    1.0

In [34]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_sub = censored_unpooled_noncentered_regression(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 11893 seconds.
There were 202 divergences after tuning. Increase `target_accept` or reparameterize.
The acceptance probability does not match the target. It is 0.8671335254533363, but should be close to 0.95. Try to increase the number of tuning steps.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The rhat statistic is larger than 1.4 for some parameters. The sampler did not converge.
The estimated number of effective samples is smaller than 200 for some parameters.


In [35]:
unpooled_sub['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]    0.084  3.523  -6.244    6.946      0.578    0.412      37.0   
𝜓_offset[0]  0.518  0.143   0.274    0.784      0.049    0.036       8.0   
𝜓_offset[1]  0.068  0.105  -0.121    0.269      0.029    0.021      14.0   
𝜓_offset[2] -0.793  0.084  -0.949   -0.644      0.017    0.012      23.0   
𝜓_offset[3] -0.403  0.103  -0.591   -0.212      0.009    0.006     137.0   
...            ...    ...     ...      ...        ...      ...       ...   
𝜓[76]        0.436  3.526  -5.889    7.345      0.579    0.413      37.0   
𝜓[77]        0.317  3.526  -6.089    7.124      0.579    0.412      37.0   
𝜓[78]        0.636  3.533  -5.788    7.416      0.593    0.423      36.0   
𝜓[79]        0.156  3.523  -6.169    7.042      0.573    0.408      38.0   
𝜎[0]         0.056  0.002   0.053    0.060      0.000    0.000     386.0   

             ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]      37.0      37.0     145.0   1.10  
𝜓_offset[0]     8.0       8.0      35.0   1.41  
𝜓_offset[1]    14.0      14.0      70.0   1.21  
𝜓_offset[2]    23.0      23.0     155.0   1.13  
𝜓_offset[3]   136.0     136.0     449.0   1.03  
...             ...       ...       ...    ...  
𝜓[76]          37.0      37.0     139.0   1.10  
𝜓[77]          37.0      37.0     144.0   1.10  
𝜓[78]          36.0      36.0     134.0   1.10  
𝜓[79]          38.0      38.0     143.0   1.10  
𝜎[0]          386.0     387.0     799.0   1.00  

[165 rows x 11 columns]

In [36]:
toytrace(unpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="t27f3fad5c927443d86c2c851337731ed" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 50.0 149.15014164305947 L 54.040404040404034 150.0 L 58.080808080808076 149.71671388101984 L 62.12121212121211 149.15014164305947 L 66.16161616161615 149.71671388101984 L 70.20202020202022 148.58356940509915 L 74.24242424242422 147.45042492917847 L 78.28282828282829 147.16713881019828 L 82.32323232323233 146.88385269121812 L 86.36363636363637 147.45042492917847 L 90.40404040404042 144.61756373937678 L 94.44444444444444 143.20113314447593 L 98.48484848484847 145.18413597733712 L 102.52525252525253 144.05099150141643 L 106.56565656565655 142.91784702549575 L 110.6060606060606 140.08498583569406 L 114.64646464646464 136.40226628895184 L 118.68686868686868 141.21813031161471 L 122.72727272727272 135.55240793201133 L 126.76767676767676 131.58640226628896 L 130.8080808080808 136.68555240793202 L 134.84848484848482 129.32011331444758 L 138.88888888888889 127.90368271954674 L 142.92929292929293 123.93767705382437 L 146.96969696969694 123.37110481586402 L 151.01010101010098 119.12181303116147 L 155.05050505050505 123.08781869688386 L 159.0909090909091 119.40509915014164 L 163.1313131313131 113.17280453257789 L 167.17171717171718 113.17280453257789 L 171.21212121212122 109.77337110481585 L 175.25252525252523 100.70821529745041 L 179.29292929292927 99.0084985835694 L 183.33333333333334 86.82719546742209 L 187.37373737373736 91.643059490085 L 191.4141414141414 84.56090651558074 L 195.45454545454544 84.27762039660057 L 199.49494949494948 80.87818696883852 L 203.53535353535352 65.01416430594901 L 207.57575757575756 73.22946175637394 L 211.61616161616158 78.89518413597733 L 215.65656565656565 67.84702549575071 L 219.69696969696966 63.59773371104816 L 223.7373737373737 60.76487252124646 L 227.77777777777777 65.86402266288951 L 231.8181818181818 50.0 L 235.85858585858585 54.24929178470255 L 239.8989898989899 58.21529745042493 L 243.9393939393939 63.59773371104816 L 247.97979797979798 54.24929178470255 L 252.02020202020196 67.56373937677054 L 256.06060606060606 62.46458923512748 L 260.1010101010101 63.59773371104816 L 264.1414141414141 70.96317280453258 L 268.1818181818182 74.92917847025495 L 272.2222222222222 74.6458923512748 L 276.2626262626262 80.02832861189802 L 280.30303030303025 78.61189801699717 L 284.34343434343435 88.81019830028329 L 288.3838383838384 86.26062322946176 L 292.42424242424244 83.71104815864022 L 296.4646464646464 91.643059490085 L 300.50505050505046 93.62606232294618 L 304.54545454545456 98.1586402266289 L 308.58585858585855 100.42492917847026 L 312.6262626262626 105.52407932011332 L 316.6666666666667 114.30594900849857 L 320.70707070707067 103.82436260623228 L 324.74747474747466 109.77337110481585 L 328.7878787878788 112.60623229461757 L 332.82828282828285 117.98866855524079 L 336.8686868686868 120.25495750708214 L 340.9090909090908 119.40509915014164 L 344.9494949494949 124.78753541076487 L 348.98989898989896 127.05382436260624 L 353.030303030303 132.71954674220962 L 357.0707070707071 131.30311614730877 L 361.1111111111111 131.58640226628896 L 365.1515151515151 134.41926345609065 L 369.1919191919191 140.93484419263456 L 373.23232323232327 142.6345609065156 L 377.27272727272725 141.50141643059493 L 381.3131313131313 147.73371104815865 L 385.3535353535353 146.31728045325778 L 389.3939393939394 144.90084985835693 L 393.4343434343434 148.30028328611897 L 397.4747474747474 148.0169971671388 L 401.5151515151514 146.88385269121812 L 405.55555555555554 145.75070821529746 L 409.595

In [37]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    unpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t86bef437ecf94b6ab1d2ecfadbcd3d48" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -1.0 -0.5 0.0 0.5 ESTIMATED species velocity -1.0 -0.5 0.0 0.5 TRUE species velocity

In [38]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_sub = censored_partpooled_noncentered_regression(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝜎, 𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 4_000 tune and 4_000 draw iterations (16_000 + 16_000 draws total) took 9740 seconds.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The number of effective samples is smaller than 10% for some parameters.


In [39]:
toytrace(partpooled_sub['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="ta14f6afc7e9e464898a9926d6d0b4f50" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 120.27491795097177 149.72602739726028 L 123.2792808474479 149.72602739726028 L 126.28364374392399 149.45205479452054 L 129.2880066404001 148.90410958904113 L 132.2923695368762 149.72602739726028 L 135.2967324333523 149.72602739726028 L 138.3010953298284 148.63013698630138 L 141.30545822630452 148.90410958904113 L 144.30982112278062 149.17808219178082 L 147.31418401925674 149.17808219178082 L 150.31854691573287 147.26027397260273 L 153.322909812209 146.98630136986304 L 156.3272727086851 145.8904109589041 L 159.33163560516118 147.26027397260273 L 162.33599850163728 143.97260273972603 L 165.3403613981134 145.8904109589041 L 168.34472429458953 143.15068493150682 L 171.34908719106562 144.24657534246575 L 174.35345008754175 143.6986301369863 L 177.35781298401784 140.4109589041096 L 180.3621758804939 137.3972602739726 L 183.36653877697003 135.75342465753425 L 186.37090167344616 136.57534246575344 L 189.37526456992225 134.65753424657535 L 192.37962746639835 131.91780821917808 L 195.38399036287447 129.45205479452056 L 198.38835325935057 126.16438356164383 L 201.39271615582666 128.63013698630138 L 204.39707905230276 124.24657534246575 L 207.40144194877888 119.86301369863014 L 210.40580484525498 112.19178082191782 L 213.41016774173113 113.013698630137 L 216.4145306382072 116.02739726027399 L 219.41889353468335 113.56164383561645 L 222.42325643115944 105.6164383561644 L 225.42761932763554 108.35616438356163 L 228.43198222411166 103.15068493150686 L 231.43634512058776 94.93150684931507 L 234.4407080170639 92.73972602739725 L 237.44507091353995 86.98630136986301 L 240.4494338100161 84.79452054794521 L 243.4537967064922 79.58904109589042 L 246.4581596029683 77.94520547945206 L 249.4625224994444 79.86301369863014 L 252.46688539592049 68.9041095890411 L 255.47124829239664 59.04109589041096 L 258.47561118887273 68.35616438356165 L 261.47997408534883 67.53424657534245 L 264.484336981825 61.50684931506849 L 267.4886998783011 60.68493150684932 L 270.4930627747772 66.16438356164383 L 273.49742567125327 56.57534246575342 L 276.50178856772936 60.13698630136987 L 279.50615146420546 50.54794520547945 L 282.5105143606816 62.05479452054794 L 285.5148772571577 63.42465753424658 L 288.5192401536338 51.917808219178085 L 291.5236030501099 60.41095890410959 L 294.527965946586 65.06849315068494 L 297.5323288430621 66.16438356164383 L 300.53669173953824 72.46575342465752 L 303.54105463601434 74.93150684931507 L 306.5454175324905 78.21917808219177 L 309.5497804289665 87.8082191780822 L 312.5541433254427 94.38356164383562 L 315.5585062219187 92.73972602739725 L 318.5628691183949 106.16438356164385 L 321.56723201487097 103.15068493150686 L 324.5715949113471 108.63013698630138 L 327.5759578078232 114.93150684931507 L 330.5803207042993 113.56164383561645 L 333.5846836007754 116.57534246575344 L 336.5890464972515 121.23287671232876 L 339.5934093937276 115.75342465753424 L 342.5977722902037 125.89041095890411 L 345.60213518667985 125.89041095890411 L 348.60649808315594 126.98630136986303 L 351.6108609796321 129.72602739726028 L 354.6152238761082 133.2876712328767 L 357.6195867725843 139.5890410958904 L 360.6239496690604 138.76712328767124 L 363.62831256553653 139.31506849315068 L 366.6326754620126 139.5890410958904 L 369.6370383584888 142.6027397260274 L 372.6414012549648 144.5205479452055 L 375.6457641514409 143.97260273972603 L 378.650127047917 145.0684931506849 L 381.65448994439316 146.98630136986304 L 384.65885284086

In [40]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_sub['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tf6f417d2d213400c8af36ac59944e822" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -1 0 1 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [46]:
draw_velocity_dists(partpooled_sub['trace'], baseline = 5);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="td4c4ac79510949b593a3d85ea7e7bb54" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="269.36611236069837,250.0 269.67554556917617,250.0 269.98497877765396,250.0 270.2944119861318,250.0 270.6038451946095,250.0 270.9132784030873,250.0 271.22271161156516,250.0 271.53214482004296,250.0 271.84157802852076,250.0 272.15101123699856,250.0 272.4604444454763,250.0 272.7698776539541,250.0 273.0793108624319,250.0 273.3887440709097,250.0 273.69817727938755,250.0 274.00761048786524,250.0 274.3170436963431,250.0 274.62647690482083,250.0 274.93591011329863,250.0 275.2453433217765,250.0 275.55477653025423,250.0 275.8642097387321,250.0 276.1736429472099,250.0 276.4830761556876,250.0 276.7925093641655,250.0 277.10194257264317,250.0 277.411375781121,250.0 277.7208089895988,250.0 278.0302421980766,250.0 278.3396754065544,250.0 278.64910861503216,250.0 278.95854182350996,250.0 279.26797503198776,250.0 279.57740824046556,250.0 279.8868414489434,250.0 280.1962746574212,250.0 280.505707865899,250.0 280.81514107437675,250.0 281.12457428285455,250.0 281.43400749133235,250.0 281.74344069981015,250.0 282.05287390828795,250.0 282.36230711676575,250.0 282.6717403252435,250.0 282.9811735337213,250.0 283.2906067421991,250.0 283.60003995067683,250.0 283.9094731591547,250.0 284.2189063676325,250.0 284.5283395761103,250.0 284.83777278458814,250.0 285.1472059930659,250.0 285.4566392015436,250.0 285.7660724100214,250.0 286.0755056184992,250.0 286.3849388269771,250.0 286.6943720354549,250.0 287.0038052439327,250.0 287.3132384524104,250.0 287.6226716608882,250.0 287.932104869366,250.0 288.2415380778438,250.0 288.5509712863216,250.0 288.8604044947994,250.0 289.1698377032772,250.0 289.47927091175495,250.0 289.7887041202328,250.0 290.09813732871055,250.0 290.40757053718835,250.0 290.7170037456662,250.0 291.02643695414395,250.0 291.3358701626218,250.0 291.64530337109954,250.0 291.95473657957734,250.0 292.2641697880551,250.0 292.5736029965329,250.0 292.88303620501074,250.0 293.1924694134885,250.0 293.50190262196634,250.0 293.8113358304441,250.0 294.1207690389219,250.0 294.4302022473997,250.0 294.7396354558775,250.0 295.0490686643553,250.0 295.35850187283313,250.0 295.6679350813109,250.0 295.9773682897886,250.0 296.28680149826647,250.0 296.5962347067442,250.0 296.905667915222,250.0 297.21510112369987,250.0 297.5245343321776,250.0 297.83396754065546,250.0 298.1434007491332,250.0 298.452833957611,250.0 298.7622671660888,250.0 299.07170037456655,250.0 299.3811335830444,250.0 299.69056679152214,250.0 300.0,250.0 300.0,248.87868467529523 299.69056679152214,248.6873144380991 299.3811335830444,248.46821762334847 299.07170037456655,248.21829073703248 298.7622671660888,247.9342392745673 298.452833957611,247.6125922250192 298.1434007491332,247.249721963251 297.83396754065546,246.84186997531998 297.5245343321776,246.38517879166554 297.21510112369987,245.87573041052224 296.905667915222,245.30959138015106 296.5962347067442,244.68286457317177 296.28680149826647,243.99174753052915 295.9773682897886,243.23259707833023 295.6679350813109,242.40199973073337 295.35850187283313,241.49684718995326 295.0490686643553,240.51441604488815 294.7396354558775,239.45245055832265 294.4302022473997,238.3092472253468 294.1207690389219,237.08373958937128 293.8113358304441,235.77558162419479 293.50190262196634,234.38522783848254 293.1924694134885,232.9140081401801 292.88303620501074,231.3641954199822 292.5736029965329,229.73906378149618 292.2641697880551,228.04293536682417 291.95473657957734,226.2812138043079 291.64530337109954,224.460402

### Assess model fit

In [53]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val                                           #get the ^

In [54]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [47]:
# Slight advantage, but model is much less reliable
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

0.08871014808695626

In [48]:
# Increase tree depth to help convergence a bit more?
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

0.09981043085928838

In [55]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-24.948874847970348

In [56]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-9.608827390190793

In [71]:
data1 = az.load_arviz_data("non_centered_eight")
data2 = az.load_arviz_data("centered_eight")

In [72]:
data1

Inference data with groups:
	> posterior
	> posterior_predictive
	> sample_stats
	> prior
	> observed_data

In [73]:
data2

Inference data with groups:
	> posterior
	> posterior_predictive
	> sample_stats
	> prior
	> observed_data

In [74]:
az.compare({"data1": data1,"data2": data2})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo     p_loo     d_loo    weight       se        dse warning  \
data1    0 -30.6873  0.841888         0  0.531386  1.32814          0   False   
data2    1 -30.8104  0.954053  0.123084  0.468614  1.38516  0.0860464   False   

      loo_scale  
data1       log  
data2       log

In [77]:
pooled_az

Inference data with groups:
	> posterior
	> log_likelihood
	> sample_stats
	> observed_data

In [75]:
unpooled_az

Inference data with groups:
	> posterior
	> log_likelihood
	> sample_stats
	> observed_data
	> constant_data

In [76]:
partpooled_az

Inference data with groups:
	> posterior
	> log_likelihood
	> sample_stats
	> observed_data
	> constant_data

In [70]:
pooled_az = az.from_pymc3(trace = pooled_sub['trace'])

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/data/io_pymc3.py:91: FutureWarning: Using `from_pymc3` without the model will be deprecated in a future release. Not using the model will return less accurate and less useful results. Make sure you use the model argument or call from_pymc3 within a model context.
  FutureWarning,


In [61]:
unpooled_az = az.from_pymc3(trace = unpooled_sub['trace'])

In [63]:
partpooled_az = az.from_pymc3(trace = partpooled_sub['trace'])

In [66]:
az.compare({"pooled": pooled_az, "unpooled": unpooled_az, "partpooled": partpooled_az})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: UserWarning: Estimated shape parameter of Pareto distribution is greater than 0.7 for one or more samples. You should consider using a more robust model, this is because importance sampling is less likely to work well if the marginal posterior and LOO posterior are very different. This is more likely to happen with a non-robust model and highly influential observations.
  "Estimated shape parameter of Pareto distribution is greater than 0.7 for "
/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:684: Use

ValueError: The number of observations should be the same across all models